## Data Summary

The data on the boreholes is a `csv` file, the data on the tent locations is stored in several `geojson` files. There are several versions of the geolocation data. The raw data, quality-controlled data, and filtered quality-controlled data.

The geolocation data was crowdsourced from GIS volunteers in a satellite tagging campaign in the Tomnod platform. The raw tags refer to actual volunteer tags so it is very possible that one shelter is tagged multiple times by different volunteers, or that a non-shelter was tagged as a shelter. No checks or quality control was used to process these tags. 
 
Quality-controlled tags are tags that have gone through an algorithm to produce a confidence score that is based on the number of people who tagged the same point (agreement) and the reliability of the tagger. 


### Satellite Imagery Data Fields

##### Quality Controlled datasets

id: unique identifier

label: name for the feature type

score: the CrowdRank confidence score of the assigned attribute, relative to other tags in the dataset. (floating point 0-1 with 0=no confidence, 1= fully confident)

agreement: number of other taggers who placed the same tag type on this point

chip_url: link to a .jpg image chip hosted on aws with the identified feature in the center of the image

timestamp: Date/time in GMT of the last QC batch

acquisition_date: Date the image was collected

sensor: the DigitalGlobe satellite that captured the image

catalog_id: DigitalGlobe identifier for the image strips collected by our satellites

map_id: unique identifier for each lattice cell across the imagery

 

##### Raw Dataset

id: unique identifier

tagger_id: unique identifier of the user

map_view_id: not too helpful for you, but I can use this to link back to another table in the database for the map/image seen by the crowd

type_id: database tag for the feature type

label: name for the feature type

timestamp: time in GMT that tag was placed

##### Filtered Dataset 

At the end of the notebook I will generate a filtered dataset of all the tents that are within 15km of boreholes. The reason is that not all tagged tents have data for their water supply, and not all mapped boreholes have tents next to them. 


### Borehole Data

Two ways of importing the data, one with native python, one with pandas. This is for the quality controlled data.

In [1]:
# option 1, using native python. 

import csv

def get_borehole_data():
    with open('UNHCR_data/boreholes_wash.csv','r') as csvfile:
        reader = csv.reader(csvfile, delimiter = ',',quotechar = '"')
        for row in reader:
            yield row
            
borehole_data = get_borehole_data()

columns = next(borehole_data)

print('Length of Borehole Dataset:\n\n%s entries.\n\n\nBorehole Data Columns:\n\n%s' 
      % (str(len(list(borehole_data))),'\n'.join(columns)))

Length of Borehole Dataset:

11268 entries.


Borehole Data Columns:

﻿objectid
Iso3
Country
Site ID
Site name
Borehole name
Borehole ID
Last update
Latitude
Longitude
Elevation in m
Status
Drilling date
Depth in m
Static water level in m
Dynamic water level in m
Type of pump
Pump brand and model
Pump depth in m
Pump motor power in kWt
Energy source 
Generator brand and model
2nd generator brand and model
Generator capacity in KVA
2nd generator capacity in KVA
Casing diameter in inch
Casing material
1st screened area - from in m
1st screened area - to in m
2nd screen area - from in m
2nd screened area - to in m
3rd screen area - from: in m
3rd screened area - to in m
Aquifer type
Safe yield in m3/h
Daily pumping time in h
Date of last water quality control
Conductivity in µS
pH
Turbidity in NTU
Ammonia concentration in mg/L
Arsenic concentration in µg/L
Free chlorine concentration in mg/L
Total chlorine concentration in mg/L
Fluoride concentration in mg/L
Nitrate concentration in mg/L


In [2]:
# option 2, using pandas. 
# Pandas is convenient unless you need to have lots of exact control over what happens.

import pandas as pd

borehole_data = pd.read_csv('UNHCR_data/boreholes_wash.csv')

borehole_data.tail()

objectid Iso3 Country     Site ID    Site name      Borehole name  \
11263     17984  SDN   Sudan  SDNs001510  Wad Sharife  Western station B   
11264     17985  SDN   Sudan  SDNs001478        Abuda   Northern station   
11265     17986  SDN   Sudan  SDNs001478        Abuda   Southern station   
11266     17987  SDN   Sudan  SDNs001478        Abuda        New station   
11267      1574  JOR  Jordan  JORs004465      Zaatari                BH2   

                 Borehole ID Last update   Latitude  Longitude     ...       \
11263  SDN-SDNs001510-000004   2018-6-29  15.360400  36.443410     ...        
11264  SDN-SDNs001478-000001   2018-6-29  14.359440  35.885610     ...        
11265  SDN-SDNs001478-000002   2018-6-29  14.347530  35.890940     ...        
11266  SDN-SDNs001478-000003   2018-6-29  14.361720  35.888450     ...        
11267     JOR-JORs004465-003    2018-8-2  32.280991  36.337528     ...        

       Fluoride concentration in mg/L Nitrate concentration in mg/L  \
11263                             NaN                           NaN   
11264                            1.70                          1.76   
11265                            2.05                          1.76   
11266                            0.40                          0.01   
11267                             NaN                           NaN   

      Nitrite concentration in mg/L  \
11263                           NaN   
11264                          0.04   
11265                          0.04   
11266                          0.10   
11267                           NaN   

                                          Attachment 1  Attachment 2  \
11263                                              NaN           NaN   
11264                                              NaN           NaN   
11265                                              NaN           NaN   
11266                                              NaN           NaN   
11267  Zaatari-BH2-Z13-Well-completion_report-2012.pdf           NaN   

       Attachment 3 Attachment 4                              Comments  \
11263           NaN          NaN                                   NaN   
11264           NaN          NaN  Screen type: Johnson continuous slot   
11265           NaN          NaN  Screen type: Johnson continuous slot   
11266           NaN          NaN  Screen type: Johnson continuous slot   
11267           NaN          NaN                                   NaN   

                                     globalid  Unnamed: 53  
11263  {BD885ED3-CB9A-4E71-9969-717E44805789}          NaN  
11264  {C56D5E17-9E67-45AD-8A7F-6117939DEC02}          NaN  
11265  {2351F077-3296-4B96-AC0A-CDE646D70E90}          NaN  
11266  {2855BF8A-1085-4138-8749-21014994F7BA}          NaN  
11267  {624C0832-CC2C-48D0-9BA7-5A90148E1203}          NaN  

[5 rows x 54 columns]

### Geolocation Data

There are several files, each of which contain one big json file. The json files are easiest imported as dictionaries, where the field `features` contains a few thousand entries of data.

In [3]:
import os

geolocation_datasets = [path for path in os.listdir('UNHCR_data/') if 'json' in path]
print("The following geolocation datasets exist:\n\n%s" % '\n'.join(geolocation_datasets))

The following geolocation datasets exist:

bangladesh.geojson
africa1.geojson
africa2.geojson
western_asia.geojson


In [4]:
from json import loads

def get_json_data(filename):
    with open('UNHCR_data/'+filename,'r') as file:
        return loads(file.read())
    
for filename in geolocation_datasets:
    data = get_json_data(filename)
    print("Filename: %s\n" % filename)
    print("Dataset is imported as %s" % type(data))
    for field in data:
        print("field: %s" % field)
        print("type: %s" % type(data[field]))
        print("length: %s\n" % len(data[field]))
    print('\n'+10*'#'+'\n')
    
print("SAMPLE DATA:\n")
for item in data['features'][:5]:
    print(item,end='\n\n')

Filename: bangladesh.geojson

Dataset is imported as <class 'dict'>
field: type
type: <class 'str'>
length: 17

field: crs
type: <class 'dict'>
length: 2

field: features
type: <class 'list'>
length: 2861


##########

Filename: africa1.geojson

Dataset is imported as <class 'dict'>
field: type
type: <class 'str'>
length: 17

field: crs
type: <class 'dict'>
length: 2

field: features
type: <class 'list'>
length: 95219


##########

Filename: africa2.geojson

Dataset is imported as <class 'dict'>
field: type
type: <class 'str'>
length: 17

field: crs
type: <class 'dict'>
length: 2

field: features
type: <class 'list'>
length: 60670


##########

Filename: western_asia.geojson

Dataset is imported as <class 'dict'>
field: type
type: <class 'str'>
length: 17

field: crs
type: <class 'dict'>
length: 2

field: features
type: <class 'list'>
length: 17785


##########

SAMPLE DATA:

{'type': 'Feature', 'geometry': {'type': 'Point', 'coordinates': [43.887513, 36.472326]}, 'properties': {'id': 

## Geographically filtering the tent locations

The coordinates of both boreholes and tents are provided in terms of longitude and latitude. We can create a dataset that only includes tent data for tents that are within 50 km of a borehole.

In [5]:
import math

def distance(origin, destination):
    """
    Lifted from:
    https://stackoverflow.com/questions/19412462/getting-distance-between-two-points-based-on-latitude-longitude
    
    Calculate the Haversine distance.

    Parameters
    ----------
    origin : tuple of float
        (lat, long)
    destination : tuple of float
        (lat, long)

    Returns
    -------
    distance_in_km : float

    Examples
    --------
    >>> origin = (48.1372, 11.5756)  # Munich
    >>> destination = (52.5186, 13.4083)  # Berlin
    >>> round(distance(origin, destination), 1)
    504.2
    """
    lat1, lon1 = origin
    lat2, lon2 = destination
    radius = 6371  # km

    dlat = math.radians(lat2 - lat1)
    dlon = math.radians(lon2 - lon1)
    a = (math.sin(dlat / 2) * math.sin(dlat / 2) +
         math.cos(math.radians(lat1)) * math.cos(math.radians(lat2)) *
         math.sin(dlon / 2) * math.sin(dlon / 2))
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    d = radius * c

    return d


def to_floats(x):
    try:
        return (float(x[0]),float(x[1]))
    except:
        pass


# gets all borehole coordinates as (latitude,longitude) tuples
borehole_coordinates = sorted([to_floats(item[8:10]) for item in get_borehole_data()][1:]
, key = lambda x:x[0])

def distance_to_borehole(tent):
    # calculates the distance to the nearest borehole in km
    coord1 = tuple(tent['geometry']['coordinates'])[::-1]
    nearest = 10000
    for coord2 in borehole_coordinates:
        d = distance(coord1,coord2)
        if d <= nearest:
            nearest = d
    return nearest

In [6]:
from multiprocessing import Pool
from itertools import compress
from time import time
from json import dumps

def distance_filter(distance,max_distance = 15):
    # returns false if tent is more than 15km from nearest borehole
    if distance <= max_distance:
        return True
    else:
        return False

def write_filtered_dataset(datasets = geolocation_datasets):
    
    # overwrite file, if there is one.
    with open('filtered_geolocation_data.json','w') as file:
        file.write("")
        
    # iterates over geojsons and writes new file with tents that are near boreholes
    # new json file has different format: one 'tent' object in each row.
    p = Pool()
    for filename in datasets:
        
        print(filename)
        num_tents = 0
        t0 = time()
        
        # calculate & filter by distance
        data = get_json_data(filename)
        tents = [tent for tent in data['features']]
        distances = p.map(distance_to_borehole,tents)
        tents_within_range = compress(
            tents,
            [distance_filter(dist) for dist in distances]
        )
        
        # write to file
        with open('filtered_geolocation_data.json','a') as file:
            for tent in tents_within_range:
                num_tents +=1 
                print("tents within borehole range: %i" % num_tents,end='\r')
                file.write(dumps(tent)+'\n')
        
        print("tents within borehole range: %i" % num_tents)
        t1 = time()-t0
        print("Takes %1.1fs (%1.5fs / tent)" % (t1,t1/len(tents)))
    p.close()
    print("Done.")
    
write_filtered_dataset()

bangladesh.geojson
tents within borehole range: 1
tents within borehole range: 2
tents within borehole range: 3
tents within borehole range: 4
tents within borehole range: 5
tents within borehole range: 6
tents within borehole range: 7
tents within borehole range: 8
tents within borehole range: 9
tents within borehole range: 10
tents within borehole range: 11
tents within borehole range: 12
tents within borehole range: 13
tents within borehole range: 14
tents within borehole range: 15
tents within borehole range: 16
tents within borehole range: 17
tents within borehole range: 18
tents within borehole range: 19
tents within borehole range: 20
tents within borehole range: 21
tents within borehole range: 22
tents within borehole range: 23
tents within borehole range: 24
tents within borehole range: 25
tents within borehole range: 26
tents within borehole range: 27
tents within borehole range: 28
tents within borehole range: 29
tents within borehole range: 30
tents within borehole range: 3

tents within borehole range: 1757
tents within borehole range: 1758
tents within borehole range: 1759
tents within borehole range: 1760
tents within borehole range: 1761
tents within borehole range: 1762
tents within borehole range: 1763
tents within borehole range: 1764
tents within borehole range: 1765
tents within borehole range: 1766
tents within borehole range: 1767
tents within borehole range: 1768
tents within borehole range: 1769
tents within borehole range: 1770
tents within borehole range: 1771
tents within borehole range: 1772
tents within borehole range: 1773
tents within borehole range: 1774
tents within borehole range: 1775
tents within borehole range: 1776
tents within borehole range: 1777
tents within borehole range: 1778
tents within borehole range: 1779
tents within borehole range: 1780
tents within borehole range: 1781
tents within borehole range: 1782
tents within borehole range: 1783
tents within borehole range: 1784
tents within borehole range: 1785
tents within b

tents within borehole range: 1
tents within borehole range: 2
tents within borehole range: 3
tents within borehole range: 4
tents within borehole range: 5
tents within borehole range: 6
tents within borehole range: 7
tents within borehole range: 8
tents within borehole range: 9
tents within borehole range: 10
tents within borehole range: 11
tents within borehole range: 12
tents within borehole range: 13
tents within borehole range: 14
tents within borehole range: 15
tents within borehole range: 16
tents within borehole range: 17
tents within borehole range: 18
tents within borehole range: 19
tents within borehole range: 20
tents within borehole range: 21
tents within borehole range: 22
tents within borehole range: 23
tents within borehole range: 24
tents within borehole range: 25
tents within borehole range: 26
tents within borehole range: 27
tents within borehole range: 28
tents within borehole range: 29
tents within borehole range: 30
tents within borehole range: 31
tents within bore

tents within borehole range: 1515
tents within borehole range: 1516
tents within borehole range: 1517
tents within borehole range: 1518
tents within borehole range: 1519
tents within borehole range: 1520
tents within borehole range: 1521
tents within borehole range: 1522
tents within borehole range: 1523
tents within borehole range: 1524
tents within borehole range: 1525
tents within borehole range: 1526
tents within borehole range: 1527
tents within borehole range: 1528
tents within borehole range: 1529
tents within borehole range: 1530
tents within borehole range: 1531
tents within borehole range: 1532
tents within borehole range: 1533
tents within borehole range: 1534
tents within borehole range: 1535
tents within borehole range: 1536
tents within borehole range: 1537
tents within borehole range: 1538
tents within borehole range: 1539
tents within borehole range: 1540
tents within borehole range: 1541
tents within borehole range: 1542
tents within borehole range: 1543
tents within b

tents within borehole range: 2196
tents within borehole range: 2197
tents within borehole range: 2198
tents within borehole range: 2199
tents within borehole range: 2200
tents within borehole range: 2201
tents within borehole range: 2202
tents within borehole range: 2203
tents within borehole range: 2204
tents within borehole range: 2205
tents within borehole range: 2206
tents within borehole range: 2207
tents within borehole range: 2208
tents within borehole range: 2209
tents within borehole range: 2210
tents within borehole range: 2211
tents within borehole range: 2212
tents within borehole range: 2213
tents within borehole range: 2214
tents within borehole range: 2215
tents within borehole range: 2216
tents within borehole range: 2217
tents within borehole range: 2218
tents within borehole range: 2219
tents within borehole range: 2220
tents within borehole range: 2221
tents within borehole range: 2222
tents within borehole range: 2223
tents within borehole range: 2224
tents within b

...

tents within borehole range: 39291
tents within borehole range: 39292
tents within borehole range: 39293
tents within borehole range: 39294
tents within borehole range: 39295
tents within borehole range: 39296
tents within borehole range: 39297
tents within borehole range: 39298
tents within borehole range: 39299
tents within borehole range: 39300
tents within borehole range: 39301
tents within borehole range: 39302
tents within borehole range: 39303
tents within borehole range: 39304
tents within borehole range: 39305
tents within borehole range: 39306
tents within borehole range: 39307
tents within borehole range: 39308
tents within borehole range: 39309
tents within borehole range: 39310
tents within borehole range: 39311
tents within borehole range: 39312
tents within borehole range: 39313
tents within borehole range: 39314
tents within borehole range: 39315
tents within borehole range: 39316
tents within borehole range: 39317
tents within borehole range: 39318
tents within borehol

tents within borehole range: 41290
tents within borehole range: 41291
tents within borehole range: 41292
tents within borehole range: 41293
tents within borehole range: 41294
tents within borehole range: 41295
tents within borehole range: 41296
tents within borehole range: 41297
tents within borehole range: 41298
tents within borehole range: 41299
tents within borehole range: 41300
tents within borehole range: 41301
tents within borehole range: 41302
tents within borehole range: 41303
tents within borehole range: 41304
tents within borehole range: 41305
tents within borehole range: 41306
tents within borehole range: 41307
tents within borehole range: 41308
tents within borehole range: 41309
tents within borehole range: 41310
tents within borehole range: 41311
tents within borehole range: 41312
tents within borehole range: 41313
tents within borehole range: 41314
tents within borehole range: 41315
tents within borehole range: 41316
tents within borehole range: 41317
tents within borehol

tents within borehole range: 43290
tents within borehole range: 43291
tents within borehole range: 43292
tents within borehole range: 43293
tents within borehole range: 43294
tents within borehole range: 43295
tents within borehole range: 43296
tents within borehole range: 43297
tents within borehole range: 43298
tents within borehole range: 43299
tents within borehole range: 43300
tents within borehole range: 43301
tents within borehole range: 43302
tents within borehole range: 43303
tents within borehole range: 43304
tents within borehole range: 43305
tents within borehole range: 43306
tents within borehole range: 43307
tents within borehole range: 43308
tents within borehole range: 43309
tents within borehole range: 43310
tents within borehole range: 43311
tents within borehole range: 43312
tents within borehole range: 43313
tents within borehole range: 43314
tents within borehole range: 43315
tents within borehole range: 43316
tents within borehole range: 43317
tents within borehol

tents within borehole range: 45289
tents within borehole range: 45290
tents within borehole range: 45291
tents within borehole range: 45292
tents within borehole range: 45293
tents within borehole range: 45294
tents within borehole range: 45295
tents within borehole range: 45296
tents within borehole range: 45297
tents within borehole range: 45298
tents within borehole range: 45299
tents within borehole range: 45300
tents within borehole range: 45301
tents within borehole range: 45302
tents within borehole range: 45303
tents within borehole range: 45304
tents within borehole range: 45305
tents within borehole range: 45306
tents within borehole range: 45307
tents within borehole range: 45308
tents within borehole range: 45309
tents within borehole range: 45310
tents within borehole range: 45311
tents within borehole range: 45312
tents within borehole range: 45313
tents within borehole range: 45314
tents within borehole range: 45315
tents within borehole range: 45316
tents within borehol

tents within borehole range: 0
Takes 124.4s (0.00700s / tent)
Done.
